# Afficher le diagramme de Bode théorique du moteur

Saisir les caractéristiques trouvées du moteur

In [ ]:
# A personnaliser par l'étudiant
R = 0
L = 0
Ke = 0
Kc = Ke
Cr = 0
fv = 0
Jeq = 0

Saisir les caractéristiques du réducteur (déja fait)

In [ ]:
k = 9.68

Donner la fonction de transfert en boucle fermé du motoréducteur $\dfrac{\Omega_{mr}(p)}{U(p)}$ en fonction des caractéristiques ci-dessus

In [ ]:
# A personnaliser par l'étudiant en utilisant les variables ci dessus
K = 1
tau = 0

Tracer du diagramme de bode

In [ ]:
from scipy.signal import lti

ft = lti([K], [tau, 1])

from numpy import logspace
from scipy.signal import bode

puls = logspace(-1, 3, 1000)
wBode, gainBode, phaseBode = bode(ft, w=puls)

from matplotlib.pyplot import figure, subplot, title, semilogx, xlabel, ylabel, grid

figure(figsize=(15, 12))

subplot(211)
title('Diagrammes de Bode')
semilogx(wBode, gainBode, lw=2)
#xlabel('Pulsation (rad/s)')
ylabel('Amplitude (dB)')
grid(which='both')

subplot(212)
semilogx(wBode, phaseBode)
xlabel('Pulsation (rad/s)')
ylabel('Phase (deg)')
grid(which='both')

# Determination expérimentalement du module et du déphasage de la FTBF du motoréducteur à une pulsation donnée

Importation des fonctions utiles de la librairie `MyViz`

In [ ]:
from MyViz import commandeEnTensionSerie, afficher, arrondir

Ouvrir le fichier de l'expérience

In [ ]:
# A personnaliser si besoin par l'étudiant
nomFichier = 'gainPhase.csv'
inst, conMot, conGen, vitMot, couMot, couGen = commandeEnTensionSerie(nomFichier)

Afficher le graphique

In [ ]:
afficher(
    [
        (inst, conMot, 'mes', 'Consigne de tension du moteur (volt)'),
        (inst, vitMot, 'mes', 'Vitesse de rotation du motoréducteur (rad/s)')
    ],
    'Temps en seconde',
    'Commande en tension (série)',
    (10, 6)
)

Pour la suite, il est préférable d'avoir d'avoir un nombre entier de périodes pour chacun des signaux.

In [ ]:
import numpy as np


def retirerUnePeriodeAmont(var, num=1):
    while (len(var[num]) > 0 and var[num][0] >= 0):
        var = np.delete(var, np.s_[0], axis=1)
    while (len(var[num]) > 0 and var[num][0] < 0):
        var = np.delete(var, np.s_[0], axis=1)
    return var


def retirerUnePeriodeAval(var, num=1):
    while (len(var[num]) > 0 and var[num][-1] <= 0):
        var = np.delete(var, np.s_[-1], axis=1)   
    while (len(var[num]) > 0 and var[num][-1] > 0):
        var = np.delete(var, np.s_[-1], axis=1)
    return var


var = [inst, conMot, conGen, vitMot, couMot, couGen]
var = retirerUnePeriodeAmont(var)
var = retirerUnePeriodeAval(var)

inst, conMot, conGen, vitMot, couMot, couGen = var

Affichons les courbes obtenues et utiles

In [ ]:
afficher(
    [
        (inst, conMot, 'mes', 'Consigne : la tension du moteur'),
        (inst, vitMot, 'mes', 'Reponse : la vitesse de rotation du motoréducteur')
    ],
    'Temps en seconde',
    'Commande en tension (série)',
    (10, 6)
)

Pour faire une étude fréquentielle, il faut retirer le régime transitoire

In [ ]:
# A personnaliser si besoin par l'étudiant
combienDePeriodes = 0

var = [inst, conMot, conGen, vitMot, couMot, couGen]
for _ in range(combienDePeriodes):
    var = retirerUnePeriodeAval(var)
inst, conMot, conGen, vitMot, couMot, couGen = var

Nous allons maintenant faire une régression linéaire avec une loi en $A \cdot \sin(\omega \cdot t + \varphi) + A_0$ avec $\omega = 2 \cdot \pi \cdot f$ sur le signal d'entrée (conMot) et de sortie (vitMot)

Sur conMot<br/>
• $A$ est l'amplitude de la consigne en volt<br/>
• $A_0$ est l'offset de l'amplitude de la consigne en volt<br/>
• $f$ est la fréquence du signal en rad/s<br/>
• $\varphi$ est la phase en radian<br/>

Sur vitMot<br/>
• $A$ est l'amplitude de la vitesse du motoreducteur en rad/s<br/>
• $A_0$ est l'offset de l'amplitude de la vitesse du motoreducteur en rad/s<br/>
• $f$ est la fréquence du signal en rad/s<br/>
• $\varphi$ est la phase en radian<br/>

In [ ]:
import numpy as np
from scipy.optimize import curve_fit


# create the function we want to fit
def monSin(t, freq, amplitude, phase, offset):
    return amplitude * np.sin(2 * np.pi * freq * t + phase) + offset


nbPeriode = 1
for i in range(len(inst)-1):
    if conMot[i] < 0 < conMot[i+1]:
        nbPeriode += 1
freq = 1 / ((inst[-1]-inst[0])/nbPeriode)

instES = np.linspace(inst[0], inst[-1], 500)

freqE      = freq
amplitudeE = (max(conMot)-min(conMot))/2
phaseE     = 0.
offsetE    = np.mean(conMot)
pE         = [freqE, amplitudeE, phaseE, offsetE]
# now do the fit
fitE       = curve_fit(monSin, inst, conMot, p0=pE)
# recreate the fitted curve using the optimized parameters
#data_first_guess = monSin(inst, *p0)
modE = monSin(instES, *fitE[0])

eps        = 1/10000

freqS      = freq
amplitudeS = (max(vitMot)-min(vitMot))/2
phaseS     = 0.
offsetS    = np.mean(vitMot)
pS         = [freqS, amplitudeS, phaseS, offsetS]
# now do the fit
fitS       = curve_fit(monSin, inst, vitMot, p0=pS) #, bounds=[(-eps,-eps,-6.28319,-eps), (eps,eps,0,eps)]
#
# recreate the fitted curve using the optimized parameters
#data_first_guess = monSin(inst, *p0)
modS       = monSin(instES, *fitS[0])

freqE, amplitudeE, phaseE, offsetE = fitE[0]
freqS, amplitudeS, phaseS, offsetS = fitS[0]

if amplitudeS < 0:
    amplitudeS *= -1
    phaseS = phaseS - np.pi
if amplitudeE < 0:
    amplitudeE *= -1
    phaseE = phaseE - np.pi

Afficher le résultat

In [ ]:
print('On a nos modèles qui passent au mieux des mesures :')

from matplotlib.pyplot import figure, plot, xlabel, ylabel, legend, title, show

figure(figsize=(15,9))
plot(inst, conMot, '.', label='Consigne')
plot(instES, modE, '-', label='Modèle consigne')
plot(inst, vitMot, '.', label='Réponse')
plot(instES, modS, '-', label='Modèle réponse')
xlabel('Temps en seconde')
ylabel('Voir étiquette')
legend(loc='best')
show()

print('A partir du signal d\'entrée :')
print('------------------')
print('Fréquence (freqE)      :', arrondir(freqE), 'Hz')
print('Amplitude (amplitudeE) :', arrondir(amplitudeE), 'V')
print('Phase     (phaseE)     :', arrondir(phaseE), 'rad')
print('Offset    (offsetE)    :', arrondir(offsetE), 'V')
print()
print('A partir du signal de sortie :')
print('------------------')
print('Fréquence (freqS)      :', arrondir(freqS), 'Hz')
print('Amplitude (amplitudeS) :', arrondir(amplitudeS), 'rad/s')
print('Phase     (phaseS)     :', arrondir(phaseS), 'rad')
print('Offset    (offsetS)    :', arrondir(offsetS), 'rad/s')

En déduire la fréquence, le module et le déphasage.

On rappelle que les signaux sont de la forme $A \cdot \sin(2 \cdot \pi \cdot f \cdot t + \varphi) + A_0$

In [ ]:
# A personnaliser par l'étudiant à partir des variables ci-dessus
frequence = (freqE+freqS)/2
module = 0
dephasageRad = 0

En déduire la pulsation, le gain et le déphasage en degrès

In [ ]:
# A personnaliser par l'étudiant à partir des variables ci-dessus
pulsation = 0
gain = 0
dephasage = 0

Afficher le résultat

In [ ]:
print('Pulsation : '+arrondir(pulsation),'rad/s')
print('Gain      : '+arrondir(gain),'dB')
print('Déphasage : '+arrondir(dephasage),'°')

# Afficher le diagramme de Bode expérimental du moteur

Saisir vos différentes relevés expérimentaux

In [ ]:
wm     = [pulsation] # Pulsation mesurée
gainm  = [gain] # Gain mesuré
phasem = [dephasage] # Phase mesuré

Tracer du diagramme de bode

In [ ]:
figure(figsize=(15,12))

subplot(211)
title('Diagrammes de Bode')
semilogx(wBode, gainBode, lw=2)
semilogx(wm, gainm, '.', lw=2)
#xlabel('Pulsation (rad/s)')
ylabel('Amplitude (dB)')
grid(which='both')

subplot(212)
semilogx(wBode, phaseBode)
semilogx(wm, phasem, '.')
xlabel('Pulsation (rad/s)')
ylabel('Phase (deg)')
grid(which='both')